##CIS 5560 Term Project 
###Group 3
####Team Member : Nagender Chauhan, Suman Chauhan, Yougender Chauhan, Hsiu-Ping Lin

### Import Spark SQL and Spark ML Libraries

First, import the libraries you will need:

In [0]:
from pyspark.sql.types import *
from pyspark.sql.functions import *

from pyspark.ml import Pipeline
from pyspark.ml.classification import DecisionTreeClassifier, LogisticRegression, GBTClassifier, RandomForestClassifier, LinearSVC
from pyspark.ml.feature import VectorAssembler, StringIndexer, VectorIndexer, MinMaxScaler, CountVectorizer, IDF, Tokenizer, StopWordsRemover
from pyspark.ml.tuning import ParamGridBuilder, TrainValidationSplit

from pyspark.ml.evaluation import BinaryClassificationEvaluator, MulticlassClassificationEvaluator
from pyspark.mllib.evaluation import MulticlassMetrics
from time import time

from pyspark.context import SparkContext
from pyspark.sql.session import SparkSession
from pyspark.storagelevel import StorageLevel

#####Spark Submit setting

In [0]:
IS_SPARK_SUBMIT_CLI = True
if IS_SPARK_SUBMIT_CLI:
    sc = SparkContext.getOrCreate()
    spark = SparkSession(sc)

In [0]:
# Limit the log
spark.sparkContext.setLogLevel("WARN")

### Load Source Data at Databricks
Loading the Books ratings into a DataFrame. This data consists of 3 million reviews of books.

In [0]:
##File location and type
#file_location = "/FileStore/tables/Books_rating_first10000.csv"
#file_type = "csv"
#
## CSV options
#infer_schema = "true"
#first_row_is_header = "true"
#delimiter = ","
#
## The applied options are for CSV files. For other file types, these will be ignored.
#df = spark.read.format(file_type) \
#  .option("inferSchema", infer_schema) \
#  .option("header", first_row_is_header) \
#  .option("sep", delimiter) \
#  .load(file_location)
#
#display(df)

Id Title Price User_id profileName review/helpfulness review/score review/time review/summary review/text 1882931173 Its Only Art If Its Well Hung! null AVCGYZL8FQQTD "Jim of Oz ""jim-of-oz""" 7/7 4.0 940636800 Nice collection of Julie Strain images This is only for Julie Strain fans. It's a collection of her photos -- about 80 pages worth with a nice section of paintings by Olivia.If you're looking for heavy literary content, this isn't the place to find it -- there's only about 2 pages with text and everything else is photos.Bottom line: if you only want one book, the Six Foot One ... is probably a better choice, however, if you like Julie like I like Julie, you won't go wrong on this one either. 0826414346 Dr. Seuss: American Icon null A30TK6U7DNS82R Kevin Killian 10/10 5.0 1095724800 Really Enjoyed It I don't care much for Dr. Seuss but after reading Philip Nel's book I changed my mind--that's a good testimonial to the power of Rel's writing and thinking. Rel plays Dr. Seuss the ultimate compliment of treating him as a serious poet as well as one of the 20th century's most interesting visual artists, and after reading his book I decided that a trip to the Mandeville Collections of the library at University of California in San Diego was in order, so I could visit some of the incredible Seuss/Geisel holdings they have there.There's almost too much to take in, for, like William Butler Yeats, Seuss led a career that constantly shifted and metamoprhized itself to meet new historical and political cirsumstances, so he seems to have been both a leftist and a conservative at different junctures of his career, both in politics and in art. As Nel shows us, he was once a cartoonist for the fabled PM magazine and, like Andy Warhol, he served his time slaving in the ad business too. All was in the service of amusing and broadening the minds of US children. Nel doesn't hesitate to administer a sound spanking to the Seuss industry that, since his death, has seen fit to license all kinds of awful products including the recent CAT IN THE HAT film with Mike Myers. Oh, what a cat-astrophe!The book is great and I can especially recommend the work of the picture editor who has given us a bounty of good illustrations. 0826414346 Dr. Seuss: American Icon null A3UH4UZ4RSVO82 John Granger 10/11 5.0 1078790400 Essential for every personal and Public Library "If people become the books they read and if ""the child is father to the man 0826414346 Dr. Seuss: American Icon null A2MVUWT453QH61 "Roy E. Perry ""amateur philosopher""" 7/7 4.0 1090713600 Phlip Nel gives silly Seuss a serious treatment Theodore Seuss Geisel (1904-1991), aka "Dr. Seuss," was one of the most influential writers and artists of the 20th century.In 1959, Rudolf Flesch wrote, "A hundred years from now, children and their parents will still eagerly read the books of a fellow called Ted Geisel, popularly known as Dr. Seuss."Flesch was too conservative in his prediction. A century, and more, from today, Dr. Seuss will still be read when many authors on today's bestseller lists will be forgotten.Published on the centenary of Geisel's birth, Dr. Seuss: American Icon analyzes six key aspects of Seuss's career: poetry, politics, art, biography, marketing, and influence.In six insightful chapters, Philip Nel, Assistant Professor of English at Kansas State University, discusses "U.S. Laureate of Nonsense," "Dr. Seuss vs. Adolf Hitler," "The Doc in the Smock," "The 5,000 Fingers of Dr. S.," "The Disneyfication of Dr. Seuss," and "The Cat in the Hat for President."Nel gives short shrift to Geisel's childhood and family background--and, indeed, to biography in general--preferring to focus on Seuss's writing and art, from his first book, And to Think That I Saw It on Mulberry Street (1937) to his last book, Oh, the Places You'll Go! (1990).Dr. Seuss's breakthrough year was 1957, when he published the two books with which he is most often identified: The Cat in the Hat and How the Grinch Stole

#####Read data into dataframe using pyspark

In [0]:
df = spark.read.csv('/user/hlin54/Books_rating.csv', inferSchema=True, header=True)

In [0]:
booksSchema = StructType([
  StructField("Id", IntegerType(), False),
  StructField("Title", StringType(), False),
  StructField("Price", FloatType(), False),
  StructField("User_id", StringType(), False),
  StructField("profileName", StringType(), False),
  StructField("review/helpfulness", StringType(), False),
  StructField("review/score", IntegerType(), False),
  StructField("review/time", IntegerType(), False),
  StructField("review/summary", StringType(), False),
  StructField("review/text", StringType(), False),
])

#####Pritning the total count of reviews

In [0]:
print('data count:', df.count())

data count: 10000


#####Select the column we need (for multiclass classification)

In [0]:
df_new = df.select(((col("Price")).cast("Float")), "review/summary", ((col("review/time")).cast("Float")), ((col("review/score").cast("Int")).alias("score")))

#####Remove weird values for our label column

In [0]:
df_new = df_new.filter(col("score") <= 5)

#####Replace average values to missing values(column : Price, review/time)

In [0]:
price_avg = df_new.agg({'Price': 'mean'}).collect()[0][0]
df_new = df_new.fillna(price_avg, subset = ["Price"])

time_avg = df_new.agg({'review/time': 'mean'}).collect()[0][0]
df_new = df_new.fillna(time_avg, subset = ["review/time"])


#####Drop NA values

In [0]:
df_new = df_new.na.replace("nan", None)
df_new = df_new.dropna()

#####Check the label column do not contain weird values

In [0]:
unique_names = df_new.select("score").distinct()
print("unique score")
unique_names.show()

unique score
+-----+
|score|
+-----+
|    1|
|    3|
|    5|
|    4|
|    2|
+-----+



In [0]:
df_new.show(20)

+---------+--------------------+-----------+-----+
|    Price|      review/summary|review/time|score|
+---------+--------------------+-----------+-----+
|19.570179|Nice collection o...| 9.406368E8|    4|
|19.570179|   Really Enjoyed It|1.0957248E9|    5|
|19.570179|Essential for eve...|1.0787904E9|    5|
|19.570179|Phlip Nel gives s...|1.0907136E9|    4|
|19.570179|Good academic ove...|1.1079936E9|    4|
|19.570179|One of America's ...|1.1271744E9|    4|
|19.570179|A memorably excel...|1.1001312E9|    5|
|19.570179|Academia At It's ...|   1.2312E9|    5|
|19.570179|And to think that...|1.2098592E9|    5|
|19.570179|Fascinating accou...|1.0763712E9|    4|
|     19.4|Outstanding Resou...|   9.9144E8|    5|
|     19.4|Small Churches CA...|1.2917664E9|    5|
|     19.4|Not Just for Past...|1.2483072E9|    5|
|     19.4|Small church past...|  1.22256E9|    5|
|    10.95|            not good|1.1170656E9|    1|
|    10.95|  Here is my opinion|1.1195712E9|    4|
|    10.95|        Buyer beware

#####Check the data do not contain missing values

In [0]:
df_new.select([count(when(isnull(c), c)).alias(c) for c in df_new.columns]).show()

+-----+--------------+-----------+-----+
|Price|review/summary|review/time|score|
+-----+--------------+-----------+-----+
|    0|             0|          0|    0|
+-----+--------------+-----------+-----+



###Split whole data into train and test data

#### Split the Data
In common with most classification modeling processes, you'll split the data into a set for training, and a set for testing the trained model. When building supervised machine learning models to split the source data, using some of it to train the model and reserving some to test the trained model. In this exercise, you will use 70% of the data for training, and reserve 30% for testing. In the testing data, the **label** column is renamed to **trueLabel** so you can use it later to compare predicted labels with known actual values.

In [0]:
train, test = df_new.randomSplit([0.7, 0.3])

#####Transfer and assemble the features we need

A predictive model often requires multiple stages of feature preparation. For example, it is common when using some algorithms to distingish between continuous features (which have a calculable numeric value) and categorical features (which are numeric representations of discrete categories). It is also common to *normalize* continuous numeric features to use a common scale (for example, by scaling all numbers to a proportinal decimal value between 0 and 1).

A pipeline consists of a a series of *transformer* and *estimator* stages that typically prepare a DataFrame for
modeling and then train a predictive model. In this case, you will create a pipeline with seven stages:
- A **StringIndexer** estimator that converts string values to indexes for categorical features
- A **VectorAssembler** that combines categorical features into a single vector
- A **VectorIndexer** that creates indexes for a vector of categorical features
- A **VectorAssembler** that creates a vector of continuous numeric features
- A **MinMaxScaler** that normalizes continuous numeric features
- A **VectorAssembler** that creates a vector of categorical and continuous features
- A **Tokenizer** to split the tweets into individual words.
- A **StopWordsRemover** to remove common words such as "a" or "the" that have little predictive value.
- A **IDF** class to generate numeric vectors from the text values.
- A **LogisticRegression algorithm** to train a classification model.

### Define the Pipeline
The pipeline for the model consist of the following stages:

In [0]:
numVect1 = VectorAssembler(inputCols = ["Price"], outputCol="numFeatures1")
minMax1 = MinMaxScaler(inputCol = numVect1.getOutputCol(), outputCol="normFeatures1")

numVect2 = VectorAssembler(inputCols = ["review/time"], outputCol="numFeatures2")
minMax2 = MinMaxScaler(inputCol = numVect2.getOutputCol(), outputCol="normFeatures2")

tokenizer1 = Tokenizer(inputCol="review/summary", outputCol="words1")
stopwords_remover1 = StopWordsRemover(inputCol='words1',outputCol='filtered_tokens1')
cv1 = CountVectorizer(vocabSize=2**16, inputCol="filtered_tokens1", outputCol='cv1')
idf1 = IDF(inputCol='cv1', outputCol="features1", minDocFreq=5)

featVect = VectorAssembler(inputCols=["normFeatures1", "normFeatures2", "features1"], outputCol="features")

label_stringIdx = StringIndexer(inputCol = "score", outputCol = "label")


###Multi Classification

####1.Logistic Regression

In [0]:
lr = LogisticRegression(labelCol="label",featuresCol="features")
pipeline_lr = Pipeline(stages=[numVect1, minMax1, numVect2, minMax2, tokenizer1, stopwords_remover1, cv1, idf1, featVect, label_stringIdx, lr])

#####Setting Logistic Regression parameters

In [0]:
paramGrid_lr = (ParamGridBuilder() \
             .addGrid(lr.regParam, [0.01, 0.5]) \
             .addGrid(lr.elasticNetParam, [0.0, 0.5]) \
             .addGrid(lr.maxIter, [5, 15]) \
             .build())

#####Using TrainValidationSplit or CrossValidator and model training time of Logistic Regression
here we're using TrainValidationSplit

In [0]:
start3 = time()

tv_lr = TrainValidationSplit(estimator=pipeline_lr, evaluator=MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_lr, trainRatio=0.7)
#cv_lr= cv = CrossValidator(estimator=pipeline_lr, evaluator= MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_lr)
model_lr = tv_lr.fit(train)

end3 = time()
phrase = 'LogisticRegression testing'
print('{} takes {} seconds'.format(phrase, (end3 - start3))) #round(end - start, 2)))


/databricks/spark/python/pyspark/ml/util.py:886: UserWarning: Cannot find mlflow module. To enable MLflow logging, install mlflow from PyPI.
  warnings.warn(_MLflowInstrumentation._NO_MLFLOW_WARNING)
LogisticRegression testing takes 208.23389077186584 seconds


#####Evaluate the performance of Logistic Regression

In [0]:
predictions_lr = model_lr.transform(test)

evaluator = MulticlassClassificationEvaluator(labelCol = 'label', predictionCol="prediction")


precision = evaluator.evaluate(predictions_lr, {evaluator.metricName: "weightedPrecision"})
recall = evaluator.evaluate(predictions_lr, {evaluator.metricName: "weightedRecall"})
accuracy = evaluator.evaluate(predictions_lr, {evaluator.metricName: "accuracy"})
F1 = evaluator.evaluate(predictions_lr, {evaluator.metricName: "f1"})

# Print the evaluation metrics
print("LogisticRegression")
print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)
print("F1:", F1)

LogisticRegression
Accuracy: 0.576271186440678
Precision: 0.510485646755633
Recall: 0.576271186440678
F1: 0.5156199575347201


In [0]:
predictions_lr.show(5)

+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
|Price|      review/summary|review/time|score|       numFeatures1|       normFeatures1| numFeatures2|       normFeatures2|              words1|    filtered_tokens1|                 cv1|           features1|            features|label|       rawPrediction|         probability|prediction|
+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
| 3.99|We love Mercer Ma...| 1.210464E9|    5|[3.990000009536743]|[0.00726348312696...| [1.210464E9]|[0.7269194902082685]|[we, love, mercer

In [0]:
predictionAndLabels_lr = predictions_lr.select("prediction", "label").rdd
metrics_lr = MulticlassMetrics(predictionAndLabels_lr)
confusion_matrix_lr = metrics_lr.confusionMatrix().toArray()
print("Confusion matrix_Logistic Regression:")
print(confusion_matrix_lr)

Confusion matrix_Logistic Regression:
[[1528.  113.   40.   24.   17.]
 [ 458.  120.   35.    8.   10.]
 [ 191.   29.   26.   12.   11.]
 [ 135.   13.    7.   42.   16.]
 [ 114.   15.   12.   15.   18.]]


####2.Random Forest

In [0]:
rf = RandomForestClassifier()

pipeline_rf = Pipeline(stages=[numVect1, minMax1, numVect2, minMax2, tokenizer1, stopwords_remover1, cv1, idf1, featVect, label_stringIdx, rf])

#####Setting Random Forest parameters

In [0]:
paramGrid_rf = (ParamGridBuilder() \
             .addGrid(rf.maxDepth, [5, 10]) \
             .addGrid(rf.maxBins, [10, 20]) \
             .addGrid(rf.numTrees, [5, 20]) \
             .build())

#####Using TrainValidationSplit or CrossValidator and model training time of Random Forest
here we're using TrainValidationSplit

In [0]:
start3 = time()

tv_rf = TrainValidationSplit(estimator=pipeline_rf, evaluator=MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_rf, trainRatio=0.7)
#cv_rf= cv = CrossValidator(estimator=pipeline_rf, evaluator= MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_rf)
model_rf = tv_rf.fit(train)

end3 = time()
phrase = 'Random Forest testing'
print('{} takes {} seconds'.format(phrase, (end3 - start3))) #round(end - start, 2)))

Random Forest testing takes 170.83718824386597 seconds


#####Evaluate the performance of Random Forest

In [0]:
predictions_rf = model_rf.transform(test)

evaluator = MulticlassClassificationEvaluator(labelCol = 'label', predictionCol="prediction")

precision = evaluator.evaluate(predictions_rf, {evaluator.metricName: "weightedPrecision"})
recall = evaluator.evaluate(predictions_rf, {evaluator.metricName: "weightedRecall"})
accuracy = evaluator.evaluate(predictions_rf, {evaluator.metricName: "accuracy"})
F1 = evaluator.evaluate(predictions_rf, {evaluator.metricName: "f1"})

# Print the evaluation metrics
print("Random Forest")
print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)
print("F1:", F1)

Random Forest
Accuracy: 0.5729478231970755
Precision: 0.37502661675651694
Recall: 0.5729478231970754
F1: 0.4181770349789136


In [0]:
predictions_rf.show(5)

+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
|Price|      review/summary|review/time|score|       numFeatures1|       normFeatures1| numFeatures2|       normFeatures2|              words1|    filtered_tokens1|                 cv1|           features1|            features|label|       rawPrediction|         probability|prediction|
+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
| 3.99|We love Mercer Ma...| 1.210464E9|    5|[3.990000009536743]|[0.00726348312696...| [1.210464E9]|[0.7269194902082685]|[we, love, mercer

In [0]:
predictionAndLabels_rf = predictions_rf.select("prediction", "label").rdd
metrics_rf = MulticlassMetrics(predictionAndLabels_rf)
confusion_matrix_rf = metrics_rf.confusionMatrix().toArray()
print("Confusion matrix_Random Forest:")
print(confusion_matrix_rf)

Confusion matrix_Random Forest:
[[1.722e+03 0.000e+00 0.000e+00 0.000e+00 0.000e+00]
 [6.310e+02 0.000e+00 0.000e+00 0.000e+00 0.000e+00]
 [2.680e+02 0.000e+00 0.000e+00 1.000e+00 0.000e+00]
 [2.110e+02 0.000e+00 0.000e+00 2.000e+00 0.000e+00]
 [1.740e+02 0.000e+00 0.000e+00 0.000e+00 0.000e+00]]


####3.Decision Tree

In [0]:
dt = DecisionTreeClassifier()

pipeline_dt = Pipeline(stages=[numVect1, minMax1, numVect2, minMax2, tokenizer1, stopwords_remover1, cv1, idf1, featVect, label_stringIdx, dt])

#####Setting Decision Tree parameters

In [0]:
paramGrid_dt = (ParamGridBuilder()
             .addGrid(dt.impurity, ["gini", "entropy"])
             .addGrid(dt.maxDepth, [15, 25])
             .build())

#####Using TrainValidationSplit or CrossValidator and model training time of Decision Tree
here we're using TrainValidationSplit

In [0]:
start3 = time()

tv_dt = TrainValidationSplit(estimator=pipeline_dt, evaluator=MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_dt, trainRatio=0.7)
#cv_dt= cv = CrossValidator(estimator=pipeline_dt, evaluator= MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_dt)
model_dt = tv_dt.fit(train)

end3 = time()
phrase = 'Decision Tree testing'
print('{} takes {} seconds'.format(phrase, (end3 - start3))) #round(end - start, 2)))

Decision Tree testing takes 172.22013568878174 seconds


#####Evaluate the performance of Decision Tree

In [0]:
predictions_dt = model_dt.transform(test)

evaluator = MulticlassClassificationEvaluator(labelCol = 'label', predictionCol="prediction")

precision = evaluator.evaluate(predictions_dt, {evaluator.metricName: "weightedPrecision"})
recall = evaluator.evaluate(predictions_dt, {evaluator.metricName: "weightedRecall"})
accuracy = evaluator.evaluate(predictions_dt, {evaluator.metricName: "accuracy"})
F1 = evaluator.evaluate(predictions_dt, {evaluator.metricName: "f1"})

# Print the evaluation metrics
print("Decision Tree")
print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)
print("F1:", F1)

Decision Tree
Accuracy: 0.576271186440678
Precision: 0.5048047274438262
Recall: 0.5762711864406779
F1: 0.47610839126762416


In [0]:
predictions_dt.show(5)

+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
|Price|      review/summary|review/time|score|       numFeatures1|       normFeatures1| numFeatures2|       normFeatures2|              words1|    filtered_tokens1|                 cv1|           features1|            features|label|       rawPrediction|         probability|prediction|
+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
| 3.99|We love Mercer Ma...| 1.210464E9|    5|[3.990000009536743]|[0.00726348312696...| [1.210464E9]|[0.7269194902082685]|[we, love, mercer

In [0]:
predictionAndLabels_dt = predictions_dt.select("prediction", "label").rdd
metrics_dt = MulticlassMetrics(predictionAndLabels_dt)
confusion_matrix_dt = metrics_dt.confusionMatrix().toArray()
print("Confusion matrix_Decision Tree:")
print(confusion_matrix_dt)

Confusion matrix_Decision Tree:
[[1.628e+03 6.700e+01 1.400e+01 6.000e+00 7.000e+00]
 [5.440e+02 6.200e+01 1.700e+01 4.000e+00 4.000e+00]
 [2.310e+02 1.300e+01 1.700e+01 3.000e+00 5.000e+00]
 [1.840e+02 1.000e+00 5.000e+00 1.600e+01 7.000e+00]
 [1.460e+02 8.000e+00 2.000e+00 7.000e+00 1.100e+01]]


####Reload data for Binary Classification

In [0]:
df = spark.read.csv('/user/hlin54/Books_rating.csv', inferSchema=True, header=True)

In [0]:
print('data count:', df.count())

data count: 10000


#####Remove weird values for our label column

In [0]:
df_new = df.filter(col("review/score") <= 5)

#####Select the column we need (for binary classification)

In [0]:
df_new = df_new.select(((col("Price")).cast("Float")), "review/summary", ((col("review/time")).cast("Float")), ((col("review/score")>3).cast("Int").alias("score")))

#####Replace average values to missing values(column : Price, review/time)

In [0]:
price_avg = df_new.agg({'Price': 'mean'}).collect()[0][0]
df_new = df_new.fillna(price_avg, subset = ["Price"])

time_avg = df_new.agg({'review/time': 'mean'}).collect()[0][0]
df_new = df_new.fillna(time_avg, subset = ["review/time"])

#####Drop NA values

In [0]:
df_new = df_new.na.replace("nan", None)
df_new = df_new.dropna()

#####Check the label column do not contain weird values

In [0]:
unique_names = df_new.select("score").distinct()
print("unique score")
unique_names.show()

unique score
+-----+
|score|
+-----+
|    1|
|    0|
+-----+



In [0]:
df_new.show(20)

+---------+--------------------+-----------+-----+
|    Price|      review/summary|review/time|score|
+---------+--------------------+-----------+-----+
|19.570179|Nice collection o...| 9.406368E8|    1|
|19.570179|   Really Enjoyed It|1.0957248E9|    1|
|19.570179|Essential for eve...|1.0787904E9|    1|
|19.570179|Phlip Nel gives s...|1.0907136E9|    1|
|19.570179|Good academic ove...|1.1079936E9|    1|
|19.570179|One of America's ...|1.1271744E9|    1|
|19.570179|A memorably excel...|1.1001312E9|    1|
|19.570179|Academia At It's ...|   1.2312E9|    1|
|19.570179|And to think that...|1.2098592E9|    1|
|19.570179|Fascinating accou...|1.0763712E9|    1|
|     19.4|Outstanding Resou...|   9.9144E8|    1|
|     19.4|Small Churches CA...|1.2917664E9|    1|
|     19.4|Not Just for Past...|1.2483072E9|    1|
|     19.4|Small church past...|  1.22256E9|    1|
|    10.95|            not good|1.1170656E9|    0|
|    10.95|  Here is my opinion|1.1195712E9|    1|
|    10.95|        Buyer beware

#####Check the data do not contain missing values

In [0]:
df_new.select([count(when(isnull(c), c)).alias(c) for c in df_new.columns]).show()

+-----+--------------+-----------+-----+
|Price|review/summary|review/time|score|
+-----+--------------+-----------+-----+
|    0|             0|          0|    0|
+-----+--------------+-----------+-----+



#####Split whole data into train and test data

In [0]:
train, test = df_new.randomSplit([0.7, 0.3])

#####Transfer and assemble the features we need

In [0]:
numVect1 = VectorAssembler(inputCols = ["Price"], outputCol="numFeatures1")
minMax1 = MinMaxScaler(inputCol = numVect1.getOutputCol(), outputCol="normFeatures1")

numVect2 = VectorAssembler(inputCols = ["review/time"], outputCol="numFeatures2")
minMax2 = MinMaxScaler(inputCol = numVect2.getOutputCol(), outputCol="normFeatures2")

tokenizer1 = Tokenizer(inputCol="review/summary", outputCol="words1")
stopwords_remover1 = StopWordsRemover(inputCol='words1',outputCol='filtered_tokens1')
cv1 = CountVectorizer(vocabSize=2**16, inputCol="filtered_tokens1", outputCol='cv1')
idf1 = IDF(inputCol='cv1', outputCol="features1", minDocFreq=5)

featVect = VectorAssembler(inputCols=["numFeatures1", "normFeatures2", "features1"], outputCol="features")

label_stringIdx = StringIndexer(inputCol = "score", outputCol = "label")

###Binary Classification

####4.Gradient-boosted tree classifier

In [0]:
gbt = GBTClassifier(labelCol="label",featuresCol="features")
pipeline_gbt = Pipeline(stages=[numVect1, minMax1, numVect2, minMax2, tokenizer1, stopwords_remover1, cv1, idf1, featVect, label_stringIdx, gbt])

#####Setting GBT parameters

In [0]:
paramGrid_gbt = (ParamGridBuilder()
             .addGrid(gbt.maxDepth, [2, 6])
             .addGrid(gbt.maxBins, [15, 25])
             .addGrid(gbt.maxIter, [15, 25])
             .build())

#####Using TrainValidationSplit or CrossValidator and model training time of GBT
here we're using TrainValidationSplit

In [0]:
start3 = time()

tv_gbt = TrainValidationSplit(estimator=pipeline_gbt, evaluator=BinaryClassificationEvaluator(), estimatorParamMaps=paramGrid_gbt, trainRatio=0.7)
#cv_gbt= cv = CrossValidator(estimator=pipeline_gbt, evaluator= MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_gbt)
model_gbt = tv_gbt.fit(train)

end3 = time()
phrase = 'GBTClassifier testing'
print('{} takes {} seconds'.format(phrase, (end3 - start3))) #round(end - start, 2)))

GBTClassifier testing takes 1167.886074066162 seconds


#####Evaluate the performance of GBT

In [0]:
predictions_gbt = model_gbt.transform(test)

evaluator = MulticlassClassificationEvaluator(labelCol = 'label', predictionCol="prediction")

precision = evaluator.evaluate(predictions_gbt, {evaluator.metricName: "weightedPrecision"})
recall = evaluator.evaluate(predictions_gbt, {evaluator.metricName: "weightedRecall"})
accuracy = evaluator.evaluate(predictions_gbt, {evaluator.metricName: "accuracy"})
F1 = evaluator.evaluate(predictions_gbt, {evaluator.metricName: "f1"})

# Print the evaluation metrics
print("GBT Classifier")
print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)
print("F1:", F1)

GBT Classifier
Accuracy: 0.8052121617106582
Precision: 0.8021476823142185
Recall: 0.8052121617106582
F1: 0.742088078732878


In [0]:
predictions_gbt.show(5)

+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
|Price|      review/summary|review/time|score|       numFeatures1|       normFeatures1| numFeatures2|       normFeatures2|              words1|    filtered_tokens1|                 cv1|           features1|            features|label|       rawPrediction|         probability|prediction|
+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
| 3.99|Little Critter's ...|1.1378016E9|    1|[3.990000009536743]|[0.00526315748271...|[1.1378016E9]|[0.5962076468759714]|[little, critter'

In [0]:
predictionAndLabels_gbt = predictions_gbt.select("prediction", "label").rdd
metrics_gbt = MulticlassMetrics(predictionAndLabels_gbt)
confusion_matrix_gbt = metrics_gbt.confusionMatrix().toArray()
print("Confusion matrix_GBT:")
print(confusion_matrix_gbt)

Confusion matrix_GBT:
[[2339.   19.]
 [ 564.   71.]]


####5.Linear Support Vector Machine (LinearSVC)

In [0]:
lsvc = LinearSVC(labelCol="label",featuresCol="features")
pipeline_lsvc = Pipeline(stages=[numVect1, minMax1, numVect2, minMax2, tokenizer1, stopwords_remover1, cv1, idf1, featVect, label_stringIdx, lsvc])

#####Setting LinearSVC parameters

In [0]:
paramGrid_lsvc = (ParamGridBuilder()
             .addGrid(lsvc.regParam, [0.01, 0.5]) \
             .addGrid(lsvc.maxIter, [5, 15]) \
             .build())

#####Using TrainValidationSplit or CrossValidator and model training time of LinearSVC
here we're using TrainValidationSplit

In [0]:
start3 = time()

tv_lsvc = TrainValidationSplit(estimator=pipeline_lsvc, evaluator=BinaryClassificationEvaluator(), estimatorParamMaps=paramGrid_lsvc, trainRatio=0.7)
#cv_lsvc= cv = CrossValidator(estimator=pipeline_lsvc, evaluator= MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_lsvc)
model_lsvc = tv_lsvc.fit(train)

end3 = time()
phrase = 'LinearSVC testing'
print('{} takes {} seconds'.format(phrase, (end3 - start3))) #round(end - start, 2)))

LinearSVC testing takes 117.5961503982544 seconds


#####Evaluate the performance of LinearSVC

In [0]:
predictions_lsvc = model_lsvc.transform(test)

evaluator = MulticlassClassificationEvaluator(labelCol = 'label', predictionCol="prediction")

precision = evaluator.evaluate(predictions_lsvc, {evaluator.metricName: "weightedPrecision"})
recall = evaluator.evaluate(predictions_lsvc, {evaluator.metricName: "weightedRecall"})
accuracy = evaluator.evaluate(predictions_lsvc, {evaluator.metricName: "accuracy"})
F1 = evaluator.evaluate(predictions_lsvc, {evaluator.metricName: "f1"})

# Print the evaluation metrics
print("LinearSVC")
print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)
print("F1:", F1)

LinearSVC
Accuracy: 0.8102238556632142
Precision: 0.789295985796806
Recall: 0.8102238556632142
F1: 0.7667406648590335


In [0]:
predictions_lsvc.show(5)

+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+----------+
|Price|      review/summary|review/time|score|       numFeatures1|       normFeatures1| numFeatures2|       normFeatures2|              words1|    filtered_tokens1|                 cv1|           features1|            features|label|       rawPrediction|prediction|
+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+----------+
| 3.99|Little Critter's ...|1.1378016E9|    1|[3.990000009536743]|[0.00526315748271...|[1.1378016E9]|[0.5962076468759714]|[little, critter'...|[little, critter'...|(7506,[36,40,190,...|(7506,[36,40,190,

In [0]:
predictionAndLabels_lsvc = predictions_lsvc.select("prediction", "label").rdd
metrics_lsvc = MulticlassMetrics(predictionAndLabels_lsvc)
confusion_matrix_lsvc = metrics_lsvc.confusionMatrix().toArray()
print("Confusion matrix_LinearSVC:")
print(confusion_matrix_lsvc)

Confusion matrix_LinearSVC:
[[2298.   60.]
 [ 508.  127.]]


####6.Logistic Regression (for binary classification)

In [0]:
lr = LogisticRegression(labelCol="label",featuresCol="features")
pipeline_lr = Pipeline(stages=[numVect1, minMax1, numVect2, minMax2, tokenizer1, stopwords_remover1, cv1, idf1, featVect, label_stringIdx, lr])

#####Setting Logistic Regression parameters

In [0]:
paramGrid_lr = (ParamGridBuilder() \
             .addGrid(lr.regParam, [0.01, 0.5]) \
             .addGrid(lr.elasticNetParam, [0.0, 0.5]) \
             .addGrid(lr.maxIter, [5, 15]) \
             .build())

#####Using TrainValidationSplit or CrossValidator and model training time of Logistic Regression(Binary)
here we're using TrainValidationSplit

In [0]:
start3 = time()

tv_lr = TrainValidationSplit(estimator=pipeline_lr, evaluator=MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_lr, trainRatio=0.7)
#cv_lr= cv = CrossValidator(estimator=pipeline_lr, evaluator= MulticlassClassificationEvaluator(), estimatorParamMaps=paramGrid_lr)
model_lr = tv_lr.fit(train)

end3 = time()
phrase = 'LogisticRegression(Binary) testing'
print('{} takes {} seconds'.format(phrase, (end3 - start3))) #round(end - start, 2)))

LogisticRegression testing takes 111.29269742965698 seconds


#####Evaluate the performance of Logistic Regression

In [0]:
predictions_lr = model_lr.transform(test)

evaluator = MulticlassClassificationEvaluator(labelCol = 'label', predictionCol="prediction")


precision = evaluator.evaluate(predictions_lr, {evaluator.metricName: "weightedPrecision"})
recall = evaluator.evaluate(predictions_lr, {evaluator.metricName: "weightedRecall"})
accuracy = evaluator.evaluate(predictions_lr, {evaluator.metricName: "accuracy"})
F1 = evaluator.evaluate(predictions_lr, {evaluator.metricName: "f1"})

# Print the evaluation metrics
print("LogisticRegression(Binary)")
print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)
print("F1:", F1)

LogisticRegression
Accuracy: 0.805880387570999
Precision: 0.7781782809191232
Recall: 0.805880387570999
F1: 0.7726339871103705


In [0]:
predictions_lr.show(5)

+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
|Price|      review/summary|review/time|score|       numFeatures1|       normFeatures1| numFeatures2|       normFeatures2|              words1|    filtered_tokens1|                 cv1|           features1|            features|label|       rawPrediction|         probability|prediction|
+-----+--------------------+-----------+-----+-------------------+--------------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+--------------------+----------+
| 3.99|Little Critter's ...|1.1378016E9|    1|[3.990000009536743]|[0.00526315748271...|[1.1378016E9]|[0.5962076468759714]|[little, critter'

In [0]:
predictionAndLabels_lr = predictions_lr.select("prediction", "label").rdd
metrics_lr = MulticlassMetrics(predictionAndLabels_lr)
confusion_matrix_lr = metrics_lr.confusionMatrix().toArray()
print("Confusion matrix_Logistic Regression(Binary):")
print(confusion_matrix_lr)

Confusion matrix_Logistic Regression:
[[2254.  104.]
 [ 477.  158.]]
